In [41]:
%matplotlib inline

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px

from statsmodels.stats.outliers_influence import variance_inflation_factor
from statsmodels.tools.tools import add_constant
import statsmodels.api as sm
from statsmodels.graphics.gofplots import qqplot


from sklearn.metrics import r2_score, mean_squared_error, make_scorer
from sklearn.linear_model import LinearRegression, Lasso, Ridge, ElasticNet
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.model_selection import train_test_split, cross_val_score, KFold, GridSearchCV
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, StackingRegressor
from sklearn.svm import SVR

import optuna
import xgboost as xgb
import catboost
from catboost import CatBoostRegressor

import warnings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter('ignore', pd.errors.SettingWithCopyWarning)
warnings.simplefilter(action="ignore", category=pd.errors.PerformanceWarning)

In [3]:
train_wOrdinal = pd.read_csv('~/Documents/AmesHousingML/data_cleaning/data_ordinal.csv') 
train_originalCleaned = pd.read_csv('~/Documents/AmesHousingML/data_cleaning/data_original.csv') 
train_wOnlyDummies = pd.read_csv('~/Documents/AmesHousingML/data_cleaning/data_dummies.csv') 
train_wOnlyDummiesNoDrop = pd.read_csv('~/Documents/AmesHousingML/data_cleaning/data_dummies_noDrop.csv') 

In [64]:
frame = train_wOnlyDummiesNoDrop.copy()
frame1 = train_wOrdinal.copy()
frame2 = train_wOnlyDummiesNoDrop.copy()

Make a stacked with 

catboost_tuned	dummifiedNoDrop_onlyNormalCondition	0.949319	15834.922426

xgboost_tuned	dummifiedNoDrop_allOutliers	0.925722	20405.640534

scikit_gb_tuned	ordinal_threeXOutlier	0.920995	18588.952882

In [7]:
# Create a KFold object
kf = KFold(n_splits=5, shuffle=True, random_state=42)

In [5]:
def rmse_scorer(y_true, y_pred):
    mse = mean_squared_error(y_true, y_pred)
    rmse = np.sqrt(mse)
    return rmse

# Define the scoring function using neg_mean_squared_error
scorer = make_scorer(rmse_scorer)

In [8]:
#catboost_tuned dummifiedNoDrop_onlyNormalCondition 0.949319 15834.922426
dataset = 'dummifiedNoDrop'
model_name = 'catboost_tuned'
trial = "onlyNormalCondition"        

#below is filtering out the houses that sold in normal condition

frame = frame[frame['SaleCondition_Normal'] == 1.0]

#the features will be X (independent variables)
X = frame.drop('SalePrice', axis=1)
X_array = X.values
#the target (dependent variable) will be y
y = frame['SalePrice']
y_array = y.values

# params = {'iterations': 499, 'learning_rate': 0.0875029872444346, 'depth': 5, 'loss_function': 'RMSE', 'random_seed': 42} Mean R^2: 0.9491209951386228 
params = {'iterations': 434, 'learning_rate': 0.10599212903564667, 'depth': 5, 'loss_function': 'RMSE', 'random_seed': 42}

#Input parameters into the model
catboost_model = CatBoostRegressor(**params)

# Perform cross-validation
catboost_model_cv_scores = cross_val_score(catboost_model, X, y, cv=kf, scoring='r2')


# Use cross_val_score with the defined scorer
catboost_model_rmse_scores = cross_val_score(catboost_model, X, y, cv=kf, scoring=scorer)


0:	learn: 63387.5913987	total: 61.3ms	remaining: 26.5s
1:	learn: 59038.7428436	total: 62.7ms	remaining: 13.6s
2:	learn: 55146.8136484	total: 64.1ms	remaining: 9.2s
3:	learn: 51538.8285271	total: 65.2ms	remaining: 7.01s
4:	learn: 48206.4370746	total: 67.1ms	remaining: 5.76s
5:	learn: 45188.3123980	total: 68.3ms	remaining: 4.87s
6:	learn: 42687.0753543	total: 69.5ms	remaining: 4.24s
7:	learn: 40323.2345785	total: 70.7ms	remaining: 3.77s
8:	learn: 38160.9607223	total: 72ms	remaining: 3.4s
9:	learn: 36245.9697482	total: 73.4ms	remaining: 3.11s
10:	learn: 34619.3519759	total: 74.7ms	remaining: 2.87s
11:	learn: 33125.3677865	total: 76.1ms	remaining: 2.68s
12:	learn: 31725.8116289	total: 77.5ms	remaining: 2.51s
13:	learn: 30352.3259741	total: 78.7ms	remaining: 2.36s
14:	learn: 29162.8305331	total: 80ms	remaining: 2.23s
15:	learn: 28064.0470120	total: 81.3ms	remaining: 2.12s
16:	learn: 27021.2352883	total: 82.6ms	remaining: 2.02s
17:	learn: 26117.2359648	total: 84.1ms	remaining: 1.94s
18:	lear

In [10]:
#scikit_gb_tuned ordinal_threeXOutlier 0.920995 18588.952882
dataset = 'ordinal'
model_name = 'scikit_gb_tuned'
trial = "threeXOutlier"

#below is filtering out the 3*IQR range if the trial is for that purpose
outlier_threshold = 3
Q1 = frame1['SalePrice'].quantile(.25)
Q3 = frame1['SalePrice'].quantile(.75)
IQR = Q3 - Q1
new_bounds = Q3 + outlier_threshold * IQR
frame1.drop(frame1[frame1['SalePrice'] > new_bounds].index, axis=0, inplace = True)


#the features will be X (independent variables)
X = frame1.drop('SalePrice', axis=1)
X_array = X.values
#the target (dependent variable) will be y
y = frame1['SalePrice']
y_array = y.values

#Split your training and testing sets of data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

#params = {'n_estimators': 100,'learning_rate': 0.1,'max_depth': 3, 'random_state': 42}
params = {'n_estimators': 488, 'learning_rate': 0.09127662860772781, 'max_depth': 3, 'random_state': 42}

#Input parameters into the model
gb_model = GradientBoostingRegressor(**params)

# Train the model on the training set
gb_model.fit(X_train, y_train)

# Make predictions on the test set
gb_model_y_pred = gb_model.predict(X_test)


# Perform cross-validation
gb_model_cv_scores = cross_val_score(gb_model, X, y, cv=kf, scoring='r2')


# Use cross_val_score with the defined scorer
gb_model_rmse_scores = cross_val_score(gb_model, X, y, cv=kf, scoring=scorer)


In [89]:
#xgboost_tuned dummifiedNoDrop_allOutliers 0.925722 20405.640534
dataset = 'dummifiedNoDrop'
model_name = 'xgboost_tuned'
trial = "allOutliers"


#the features will be X (independent variables)
X = frame2.drop('SalePrice', axis=1)
X_array = X.values
#the target (dependent variable) will be y
y = frame2['SalePrice']
y_array = y.values

#Split your training and testing sets of data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)



params = {'max_depth': 4, 'learning_rate': 0.00875, 'n_estimators': 3515, 'min_child_weight': 2, 
              'colsample_bytree': 0.2050378195385253, 'subsample': 0.40369887914955715, 
              'reg_alpha': 0.3301567121037565, 'reg_lambda': 0.046181862052743}

# params =  {'objective': 'reg:squarederror',
#                    'booster': 'gbtree',
#                      'max_depth': 3,
#                      'learning_rate': 0.056842782261922145,
#                      'n_estimators': 900,
#                       'random_state': 42}


xgb_model = xgb.XGBRegressor(**params)


# Train the model on the training set
xgb_model.fit(X_train, y_train)

# Make predictions on the test set
xgb_model_y_pred = xgb_model.predict(X_test)


# # Perform cross-validation
xgb_model_cv_scores = cross_val_score(xgb_model, X, y, cv=kf, scoring='r2')

# # Use cross_val_score with the defined scorer
xgb_model_rmse_scores = cross_val_score(xgb_model, X, y, cv=kf, scoring=scorer)


In [90]:
print("CatBoost Cross-Validation R^2 Scores:", catboost_model_cv_scores, '\n')
print(f"CatBoost Mean R^2: {catboost_model_cv_scores.mean()}", '\n') 
print("CatBoost Cross-Validation RMSE Scores:", catboost_model_rmse_scores, '\n')
print(f"CatBoost Mean RMSE: {catboost_model_rmse_scores.mean()}", '\n') 

print("SciKit's GB Cross-Validation R^2 Scores:", gb_model_cv_scores, '\n')
print(f"SciKit's GB Mean R^2: {gb_model_cv_scores.mean()}", '\n') 
print("SciKit's GB Cross-Validation RMSE Scores:", gb_model_rmse_scores, '\n')
print(f"SciKit's GB Mean RMSE: {gb_model_rmse_scores.mean()}", '\n') 

print("XGBoost Cross-Validation R^2 Scores:", xgb_model_cv_scores, '\n')
print(f"XGBoost Mean R^2: {xgb_model_cv_scores.mean()}", '\n') 
print("XGBoost Cross-Validation RMSE Scores:", xgb_model_rmse_scores, '\n')
print(f"XGBoost Mean RMSE: {xgb_model_rmse_scores.mean()}", '\n') 

CatBoost Cross-Validation R^2 Scores: [0.95320842 0.95714881 0.93511468 0.94769147 0.95343353] 

CatBoost Mean R^2: 0.9493193831212242 

CatBoost Cross-Validation RMSE Scores: [17243.22560896 14208.41696744 16890.14489281 15489.2888042
 15343.53585609] 

CatBoost Mean RMSE: 15834.92242590016 

SciKit's GB Cross-Validation R^2 Scores: [0.94174232 0.91477871 0.94039009 0.9296729  0.87839295] 

SciKit's GB Mean R^2: 0.9209953932889585 

SciKit's GB Cross-Validation RMSE Scores: [16755.32004976 20174.06625804 16293.34489323 17719.28840882
 22002.74479792] 

SciKit's GB Mean RMSE: 18588.95288155032 

XGBoost Cross-Validation R^2 Scores: [0.95585631 0.95283078 0.94073908 0.94965253 0.95596385] 

XGBoost Mean R^2: 0.9510085087674225 

XGBoost Cross-Validation RMSE Scores: [16748.23218603 14907.11523792 16141.51787855 15196.16645788
 14920.84705389] 

XGBoost Mean RMSE: 15582.775762854286 



In [17]:
# stacked_model = StackingRegressor(
#     estimators=[('xgboost_tuned', xgb_model), 
#                 ('catboost_tuned', catboost_model),
#                 ('scikit_gb_tuned', gb_model)],
#     final_estimator= Lasso(alpha=272)
# )

In [29]:
stackframe0 = train_wOnlyDummiesNoDrop.copy()
stackframe1 = train_wOrdinal.copy()
stackframe2 = train_wOnlyDummies.copy()

stackframes = [stackframe0, stackframe1, stackframe2]

In [21]:
for stackframe in stackframes:

    #the features will be X (independent variables)
    X = stackframe.drop('SalePrice', axis=1)
    X_array = X.values
    #the target (dependent variable) will be y
    y = stackframe['SalePrice']
    y_array = y.values
    
    #Split your training and testing sets of data
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
    
    #fit the stacked model on training data
    stacked_model.fit(X_train, y_train)

    # Make predictions on the test set
    stacked_pred = stacked_model.predict(X_test)

    # Perform cross-validation
    stacked_model_cv_scores = cross_val_score(stacked_model, X, y, cv=kf, scoring='r2')


    # Use cross_val_score with the defined scorer
    stacked_model_rmse_scores = cross_val_score(stacked_model, X, y, cv=kf, scoring=scorer)

    print("XGBoost Cross-Validation R^2 Scores:", stacked_model_cv_scores, '\n')
    print(f"XGBoost Mean R^2: {stacked_model_cv_scores.mean()}", '\n') 
    print("XGBoost Cross-Validation RMSE Scores:", stacked_model_rmse_scores, '\n')
    print(f"XGBoost Mean RMSE: {stacked_model_rmse_scores.mean()}", '\n') 

0:	learn: 70402.7129916	total: 2.61ms	remaining: 1.13s
1:	learn: 65440.5362806	total: 4.14ms	remaining: 895ms
2:	learn: 61131.9537034	total: 5.43ms	remaining: 780ms
3:	learn: 57125.6821857	total: 6.71ms	remaining: 721ms
4:	learn: 53534.8794667	total: 8.15ms	remaining: 699ms
5:	learn: 50525.6920341	total: 10.7ms	remaining: 764ms
6:	learn: 47377.0638537	total: 12ms	remaining: 733ms
7:	learn: 44558.9220214	total: 13.4ms	remaining: 713ms
8:	learn: 42351.0625752	total: 14.8ms	remaining: 697ms
9:	learn: 40221.5590642	total: 16.2ms	remaining: 687ms
10:	learn: 38514.0779499	total: 18.1ms	remaining: 697ms
11:	learn: 36824.2661083	total: 19.5ms	remaining: 687ms
12:	learn: 35282.2920253	total: 20.9ms	remaining: 678ms
13:	learn: 33797.3739621	total: 22.2ms	remaining: 666ms
14:	learn: 32574.7414863	total: 23.5ms	remaining: 657ms
15:	learn: 31463.0531020	total: 24.8ms	remaining: 648ms
16:	learn: 30315.7303945	total: 26.2ms	remaining: 643ms
17:	learn: 29398.7191495	total: 27.4ms	remaining: 633ms
18:	

/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.239e+11, tolerance: 1.195e+09
  model = cd_fast.enet_coordinate_descent(


0:	learn: 70402.7129916	total: 1.7ms	remaining: 737ms
1:	learn: 65430.5676157	total: 3.48ms	remaining: 751ms
2:	learn: 61117.4404505	total: 4.95ms	remaining: 711ms
3:	learn: 56907.6199750	total: 6.3ms	remaining: 677ms
4:	learn: 53536.2007303	total: 7.94ms	remaining: 681ms
5:	learn: 50290.5944399	total: 9.37ms	remaining: 669ms
6:	learn: 47200.5515470	total: 10.9ms	remaining: 662ms
7:	learn: 44363.6576614	total: 12.2ms	remaining: 652ms
8:	learn: 42217.4998792	total: 13.8ms	remaining: 650ms
9:	learn: 40140.7089638	total: 15.1ms	remaining: 642ms
10:	learn: 38445.9483984	total: 16.6ms	remaining: 637ms
11:	learn: 36818.4581916	total: 18.2ms	remaining: 639ms
12:	learn: 35456.6372797	total: 20ms	remaining: 647ms
13:	learn: 34004.4468149	total: 21.3ms	remaining: 638ms
14:	learn: 32706.3911809	total: 23.4ms	remaining: 653ms
15:	learn: 31552.7158927	total: 24.9ms	remaining: 651ms
16:	learn: 30524.4389771	total: 26.4ms	remaining: 647ms
17:	learn: 29677.3269802	total: 27.9ms	remaining: 645ms
18:	le

/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.380e+11, tolerance: 1.195e+09
  model = cd_fast.enet_coordinate_descent(


0:	learn: 66946.6454525	total: 1.41ms	remaining: 610ms
1:	learn: 62173.8380635	total: 2.67ms	remaining: 577ms
2:	learn: 57797.1004647	total: 3.87ms	remaining: 555ms
3:	learn: 54129.6478302	total: 5.08ms	remaining: 546ms
4:	learn: 50442.6563872	total: 6.51ms	remaining: 559ms
5:	learn: 47241.5801960	total: 8.03ms	remaining: 573ms
6:	learn: 44620.5392949	total: 9.53ms	remaining: 581ms
7:	learn: 42145.8789163	total: 10.9ms	remaining: 582ms
8:	learn: 40101.8067850	total: 12.4ms	remaining: 584ms
9:	learn: 38003.0612843	total: 13.8ms	remaining: 583ms
10:	learn: 36104.7761980	total: 15.1ms	remaining: 581ms
11:	learn: 34571.2289159	total: 16.4ms	remaining: 577ms
12:	learn: 33078.8771368	total: 17.8ms	remaining: 577ms
13:	learn: 31788.2261242	total: 19.4ms	remaining: 581ms
14:	learn: 30568.4972416	total: 20.7ms	remaining: 579ms
15:	learn: 29467.8037814	total: 22.1ms	remaining: 577ms
16:	learn: 28496.3674531	total: 23.5ms	remaining: 576ms
17:	learn: 27761.9787495	total: 24.9ms	remaining: 576ms
18

...

/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.083e+11, tolerance: 1.182e+09
  model = cd_fast.enet_coordinate_descent(


0:	learn: 70109.1925968	total: 1.69ms	remaining: 730ms
1:	learn: 65111.0597212	total: 2.91ms	remaining: 629ms
2:	learn: 61106.7896264	total: 4.17ms	remaining: 599ms
3:	learn: 57227.2343998	total: 5.46ms	remaining: 587ms
4:	learn: 53290.5483613	total: 6.75ms	remaining: 579ms
5:	learn: 50183.7196512	total: 8.72ms	remaining: 622ms
6:	learn: 47378.2332958	total: 10ms	remaining: 613ms
7:	learn: 44869.8421762	total: 11.3ms	remaining: 604ms
8:	learn: 42577.9593521	total: 12.7ms	remaining: 599ms
9:	learn: 40541.9898161	total: 14ms	remaining: 595ms
10:	learn: 38719.5363451	total: 15.3ms	remaining: 590ms
11:	learn: 36983.8663087	total: 16.8ms	remaining: 591ms
12:	learn: 35567.7130381	total: 18.2ms	remaining: 590ms
13:	learn: 34282.0361405	total: 19.4ms	remaining: 582ms
14:	learn: 32996.5646252	total: 21.3ms	remaining: 596ms
15:	learn: 31830.2446483	total: 22.8ms	remaining: 595ms
16:	learn: 30653.7562521	total: 24ms	remaining: 589ms
17:	learn: 29714.9650284	total: 25.3ms	remaining: 585ms
18:	lear

/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.558e+11, tolerance: 1.174e+09
  model = cd_fast.enet_coordinate_descent(


0:	learn: 69742.5335953	total: 1.76ms	remaining: 763ms
1:	learn: 65252.6701306	total: 3.77ms	remaining: 814ms
2:	learn: 61069.2790355	total: 5.92ms	remaining: 851ms
3:	learn: 57371.0372754	total: 7.74ms	remaining: 832ms
4:	learn: 53609.5959325	total: 9.31ms	remaining: 799ms
5:	learn: 50372.4954337	total: 10.9ms	remaining: 778ms
6:	learn: 47394.1267878	total: 14.2ms	remaining: 867ms
7:	learn: 44633.4222077	total: 16.1ms	remaining: 857ms
8:	learn: 42265.9864604	total: 18.3ms	remaining: 866ms
9:	learn: 40174.8306560	total: 20.2ms	remaining: 857ms
10:	learn: 38277.1810527	total: 22.1ms	remaining: 852ms
11:	learn: 36561.1022763	total: 24.5ms	remaining: 863ms
12:	learn: 35150.5538476	total: 26.6ms	remaining: 862ms
13:	learn: 33709.1657314	total: 28.3ms	remaining: 850ms
14:	learn: 32475.1325132	total: 30ms	remaining: 838ms
15:	learn: 31370.2976013	total: 31.7ms	remaining: 828ms
16:	learn: 30457.3887329	total: 33ms	remaining: 811ms
17:	learn: 29425.1006684	total: 34.7ms	remaining: 802ms
18:	le

/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.560e+11, tolerance: 1.176e+09
  model = cd_fast.enet_coordinate_descent(


In [23]:
#dummifiedNoDrop_onlyNormalCondition
dataset = 'dummifiedNoDrop'
model_name = 'lasso'
trial = "onlyNormalCondition"


frame = frame[frame['SaleCondition_Normal'] == 1.0]

#the features will be X (independent variables)
X = frame.drop('SalePrice', axis=1)
X_array = X.values
#the target (dependent variable) will be y
y = frame['SalePrice']
y_array = y.values


X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

lasso_model = Lasso(alpha=272)

# Fit the Lasso model on the training set
lasso_model.fit(X_train_scaled, y_train)

# Make predictions on the test set
lasso_y_pred = lasso_model.predict(X_test_scaled)


lasso_cv_scores = cross_val_score(lasso_model, X, y, scoring="r2", cv=kf)
lasso_rmse_scores = cross_val_score(lasso_model, X, y, cv=kf, scoring=scorer)

# Display the cross-validation scores
print("Cross-Validation Scores:", lasso_cv_scores, '\n')
print(f"Mean R^2: {lasso_cv_scores.mean()}", '\n') 

 # Display the cross-validation scores
print("Cross-Validation Scores:", lasso_rmse_scores, '\n')
print(f"Mean RMSE: {lasso_rmse_scores.mean()}", '\n') 
        

/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.681e+11, tolerance: 9.051e+08
  model = cd_fast.enet_coordinate_descent(
/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.884e+11, tolerance: 9.845e+08
  model = cd_fast.enet_coordinate_descent(
/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing reg

Cross-Validation Scores: [0.92844169 0.92496315 0.9181662  0.91777866 0.92961982] 

Mean R^2: 0.923793901086189 

Cross-Validation Scores: [21323.80521583 18801.89303985 18968.21806777 19419.47557641
 18863.13933529] 

Mean RMSE: 19475.30624703189 



/Users/briandrewes/anaconda3/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.975e+11, tolerance: 9.683e+08
  model = cd_fast.enet_coordinate_descent(


In [85]:
#dummifiedNoDrop_onlyNormalCondition
dataset = 'dummifiedNoDrop'
model_name = 'ridge'
trial = "onlyNormalCondition"


frame = frame[frame['SaleCondition_Normal'] == 1.0]

#the features will be X (independent variables)
X = frame.drop('SalePrice', axis=1)
X_array = X.values
#the target (dependent variable) will be y
y = frame['SalePrice']
y_array = y.values


X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

ridge_model = Ridge(alpha=15)

# Fit the Lasso model on the training set
ridge_model.fit(X_train_scaled, y_train)

# Make predictions on the test set
ridge_y_pred = ridge_model.predict(X_test_scaled)


ridge_model_cv_scores = cross_val_score(ridge_model, X, y, scoring="r2", cv=kf)
ridge_model_rmse_scores = cross_val_score(ridge_model, X, y, cv=kf, scoring=scorer)

# Display the cross-validation scores
print("Cross-Validation Scores:", ridge_model_cv_scores, '\n')
print(f"Mean R^2: {ridge_model_cv_scores.mean()}", '\n') 

 # Display the cross-validation scores
print("Cross-Validation Scores:", ridge_model_rmse_scores, '\n')
print(f"Mean RMSE: {ridge_model_rmse_scores.mean()}", '\n') 
        

Cross-Validation Scores: [0.93803976 0.93644563 0.92773839 0.9302836  0.93779265] 

Mean R^2: 0.9340600052166288 

Cross-Validation Scores: [19842.26330054 17303.62106316 17824.36084923 17881.85984737
 17734.12029709] 

Mean RMSE: 18117.245071477468 



In [91]:
stacked_model = StackingRegressor(
    estimators=[
                ('ridge', ridge_model), 
                #('lasso', lasso_model), 
                #('catboost_tuned', catboost_model),
                ('xgboost_tuned', xgb_model)
    ],
    final_estimator= LinearRegression()
)

In [92]:


#the features will be X (independent variables)
X = stackframe0.drop('SalePrice', axis=1)
X_array = X.values
#the target (dependent variable) will be y
y = stackframe0['SalePrice']
y_array = y.values

#Split your training and testing sets of data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

#fit the stacked model on training data
stacked_model.fit(X_train, y_train)

# Make predictions on the test set
stacked_pred = stacked_model.predict(X_test)

# Calculate R2 score
r2 = r2_score(y_test, stacked_pred)


# Calculate RMSE (Root Mean Squared Error)
rmse = np.sqrt(mean_squared_error(y_test, stacked_pred))



In [93]:
print(f'R2 Score: {r2}')
print(f'RMSE: {rmse}')

R2 Score: 0.9418585851757901
RMSE: 16927.782284414323
